In [2]:
import pandas as pd
import numpy as np
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.ensemble import RandomForestRegressor
import joblib
import os
from sklearn.model_selection import GridSearchCV

In [3]:
SL = pd.read_csv("C:/Users/josen/Documents/MASTER/TFM/SmartLifter.csv")

C:\Users\josen\AppData\Local\Temp\ipykernel_20784\3896501997.py:1: DtypeWarning: Columns (14) have mixed types. Specify dtype option on import or set low_memory=False.
  SL = pd.read_csv("C:/Users/josen/Documents/MASTER/TFM/SmartLifter.csv")


In [4]:
SL['BMI'] = SL['Weight_kg'] / (SL['Height_m']**2)  

In [5]:
SL['Type_x'].unique()

array(['Strength'], dtype=object)

In [6]:
SL.info()
SL.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 100800 entries, 0 to 100799
Data columns (total 24 columns):
 #   Column            Non-Null Count   Dtype  
---  ------            --------------   -----  
 0   Age               100800 non-null  int64  
 1   Gender            100800 non-null  object 
 2   Weight_kg         100800 non-null  float64
 3   Height_m          100800 non-null  float64
 4   Workout_time      100800 non-null  float64
 5   Calories_Burned   100800 non-null  float64
 6   Type_x            100800 non-null  object 
 7   Fat_Percentage    100800 non-null  float64
 8   Frequency         100800 non-null  int64  
 9   Level             100800 non-null  object 
 10  BMI               100800 non-null  float64
 11  member_id         100800 non-null  object 
 12  goal              100800 non-null  object 
 13  equipment_access  100800 non-null  object 
 14  injury            13767 non-null   object 
 15  Title             100800 non-null  object 
 16  Type_y            10

Age Gender  Weight_kg  Height_m  Workout_time  Calories_Burned    Type_x  \
0   25   Male       53.2       1.7          0.59            532.0  Strength   
1   25   Male       53.2       1.7          0.59            532.0  Strength   
2   25   Male       53.2       1.7          0.59            532.0  Strength   
3   25   Male       53.2       1.7          0.59            532.0  Strength   
4   25   Male       53.2       1.7          0.59            532.0  Strength   

   Fat_Percentage  Frequency     Level  ...  injury  \
0            28.8          3  Beginner  ...     NaN   
1            28.8          3  Beginner  ...     NaN   
2            28.8          3  Beginner  ...     NaN   
3            28.8          3  Beginner  ...     NaN   
4            28.8          3  Beginner  ...     NaN   

                                    Title    Type_y    BodyPart   Equipment  \
0                   Dumbbell spell caster  Strength  Abdominals    Dumbbell   
1  Bosu Ball Cable Crunch With Side Bends  Strength  Abdominals       Cable   
2                     Cable Seated Crunch  Strength  Abdominals       Cable   
3                            Fire Hydrant  Strength   Abductors  Bodyweight   
4                  Wide-grip barbell curl  Strength      Biceps     Barbell   

    BodyGroup exercise_id     goal_tag movement_type equipment_std  
0        Core      E00040  Hypertrophy     Isolation      Dumbbell  
1        Core      E00154  Hypertrophy     Isolation         Cable  
2        Core      E00159  Hypertrophy     Isolation         Cable  
3        Legs      E00649  Hypertrophy     Isolation    Bodyweight  
4  Upper Body      E00666  Hypertrophy     Isolation       Barbell  

[5 rows x 24 columns]

In [7]:
# Codificar variables categóricas
cat_cols = [
    'Gender',
    'Level',
    'Type_x',
    'BodyGroup',
    'BodyPart',
    'Equipment'
]

encoders = {}

for col in cat_cols:
    le = LabelEncoder()
    SL[col + '_code'] = le.fit_transform(SL[col])
    encoders[col] = le

In [8]:
# Definir features y target
feature_cols = [
    'Age', 'Gender_code', 'Weight_kg', 'Height_m', 'Frequency', 'BMI',
    'Level_code', 'Type_x_code', 'BodyGroup_code', 'BodyPart_code', 'Equipment_code'
]
X = SL[feature_cols]
y = SL['Title']

In [9]:
# Separar en train y test
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42, stratify=y
)

In [10]:
# Entrenar solo con train
model = RandomForestClassifier(
    n_estimators=30,
    max_depth=8,
    max_features='sqrt',
    min_samples_split=10,
    random_state=42,
    n_jobs=1,
    class_weight='balanced'
)
model.fit(X_train.astype('float32'), y_train)

RandomForestClassifier(class_weight='balanced', max_depth=8,
                       min_samples_split=10, n_estimators=30, n_jobs=1,
                       random_state=42)

In [11]:
from sklearn.metrics import classification_report

# Evaluar en test
y_pred = model.predict(X_test.astype('float32'))
accuracy = accuracy_score(y_test, y_pred)
print(f"Accuracy en test: {accuracy:.2f}")

print("\nReporte de clasificación:")
print(classification_report(y_test, y_pred))

Accuracy en test: 0.07

Reporte de clasificación:
                                                                     precision    recall  f1-score   support

                                                    1.5-rep push-up       0.00      0.00      0.00         9
                                                         3/4 sit-up       0.00      0.00      0.00         6
                                     30 Arms BFR Close-Grip Push-Up       0.00      0.00      0.00        10
                                     30 Arms BFR Dumbbell Kick-Back       0.18      0.44      0.26         9
                                        30 Arms BFR High Cable Curl       0.00      0.00      0.00         9
                                  30 Arms BFR Machine Preacher Curl       0.00      0.00      0.00        10
                                       30 Arms Barbell Skullcrusher       0.14      0.11      0.12         9
                                   30 Arms Cable Concentration Curl       0.0

c:\Users\josen\Documents\MASTER\.venv\Lib\site-packages\sklearn\metrics\_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\josen\Documents\MASTER\.venv\Lib\site-packages\sklearn\metrics\_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
c:\Users\josen\Documents\MASTER\.venv\Lib\site-packages\sklearn\metrics\_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


In [12]:
# Top-3 accuracy
print("Top-3 accuracy:", np.mean([
    y in model.classes_[np.argsort(model.predict_proba([x]))[0][::-1][:3]]
    for x, y in zip(X_test.values, y_test)
]))

c:\Users\josen\Documents\MASTER\.venv\Lib\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(


c:\Users\josen\Documents\MASTER\.venv\Lib\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
c:\Users\josen\Documents\MASTER\.venv\Lib\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
c:\Users\josen\Documents\MASTER\.venv\Lib\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
c:\Users\josen\Documents\MASTER\.venv\Lib\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but RandomForestClassifier was fitted with feature names
  warnings.warn(
c:\Users\josen\Documents\MASTER\.venv\Lib\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but 

Top-3 accuracy: 0.19905753968253967


In [13]:
# Calcular Top-5 y Top-10 accuracy
def top_n_accuracy(model, X, y_true, n=5):
    proba = model.predict_proba(X.astype('float32'))
    top_n = np.argsort(proba, axis=1)[:, -n:]
    classes = model.classes_
    y_true_idx = np.array([np.where(classes == label)[0][0] if label in classes else -1 for label in y_true])
    hits = [y_true_idx[i] in top_n[i] for i in range(len(y_true_idx))]
    return np.mean(hits)

top5_acc = top_n_accuracy(model, X_test, y_test, n=5)
top10_acc = top_n_accuracy(model, X_test, y_test, n=10)

print(f"Top-5 accuracy: {top5_acc:.2f}")
print(f"Top-10 accuracy: {top10_acc:.2f}")

Top-5 accuracy: 0.28
Top-10 accuracy: 0.42


In [14]:
# Interpretación de los resultados de Top-N Accuracy (Top-5 y Top-10)

#El Top-N accuracy es una métrica utilizada para evaluar modelos de clasificación cuando hay muchas clases posibles, como en sistemas de recomendación. En lugar de medir solo si el modelo acierta la clase exacta (Top-1), se considera un acierto si la clase verdadera está entre las N predicciones más probables del modelo.

#- Top-5 accuracy: Indica el porcentaje de veces que la clase correcta aparece entre las 5 opciones más probables sugeridas por el modelo.
#- Top-10 accuracy: Indica el porcentaje de veces que la clase correcta aparece entre las 10 opciones más probables.

#Valores bajos en estas métricas pueden reflejar la dificultad del problema y la gran cantidad de clases posibles. Sin embargo, en sistemas de recomendación, lo importante es que el modelo sea capaz de incluir opciones relevantes y variadas dentro de sus sugerencias principales, ayudando así al usuario a encontrar ejercicios adecuados, aunque no siempre acierte el único correcto.

#En resumen, un Top-N accuracy alto indica que el modelo suele incluir la respuesta correcta entre sus principales recomendaciones, lo cual es útil para personalizar y diversificar las rutinas sugeridas.#

In [15]:
# Importancia de variables
print("Importancia de variables:", dict(zip(feature_cols, model.feature_importances_)))

Importancia de variables: {'Age': np.float64(0.08350323636130103), 'Gender_code': np.float64(0.006218475022287158), 'Weight_kg': np.float64(0.04220621995698338), 'Height_m': np.float64(0.02194670779291185), 'Frequency': np.float64(0.01968387533766431), 'BMI': np.float64(0.0931684194710113), 'Level_code': np.float64(0.08437447787679701), 'Type_x_code': np.float64(0.0), 'BodyGroup_code': np.float64(0.140079050709559), 'BodyPart_code': np.float64(0.2463367356356433), 'Equipment_code': np.float64(0.2624828018358417)}


In [16]:
from sklearn.model_selection import cross_val_score

# Validación cruzada
print("CV accuracy:", cross_val_score(model, X, y, cv=3, scoring='accuracy').mean())

CV accuracy: 0.10634920634920635


In [17]:
# Cambia el target a BodyPart y repite el entrenamiento y evaluación
y_bodypart = SL['BodyPart']
X_train, X_test, y_train, y_test = train_test_split(X, y_bodypart, test_size=0.2, random_state=42, stratify=y_bodypart)
model.fit(X_train.astype('float32'), y_train)
y_pred = model.predict(X_test.astype('float32'))
print("Accuracy BodyPart:", accuracy_score(y_test, y_pred))
print(classification_report(y_test, y_pred))

Accuracy BodyPart: 0.9903273809523809
              precision    recall  f1-score   support

  Abdominals       1.00      1.00      1.00      4426
   Abductors       1.00      1.00      1.00        94
   Adductors       1.00      1.00      1.00        43
      Biceps       1.00      1.00      1.00      1295
      Calves       0.94      0.88      0.91       278
       Chest       0.99      0.96      0.97      2084
    Forearms       0.64      0.85      0.73       196
      Glutes       0.95      0.96      0.95       591
  Hamstrings       0.99      0.99      0.99       568
        Lats       1.00      1.00      1.00       966
  Lower Back       0.98      1.00      0.99       603
 Middle Back       1.00      0.99      0.99       914
        Neck       1.00      1.00      1.00        62
  Quadriceps       1.00      1.00      1.00      4295
   Shoulders       1.00      1.00      1.00      2411
       Traps       1.00      1.00      1.00       177
     Triceps       1.00      1.00      1.00

In [18]:
param_grid = {
    'n_estimators': [30, 50, 100],
    'max_depth': [6, 8, 12],
    'min_samples_split': [5, 10, 20],
    'max_features': ['sqrt', 'log2'],
    'class_weight': ['balanced']
}

grid = GridSearchCV(
    RandomForestClassifier(random_state=42, n_jobs=1),
    param_grid,
    cv=3,
    scoring='accuracy',
    verbose=2
)
grid.fit(X_train.astype('float32'), y_train)
print("Mejores parámetros:", grid.best_params_)
model = grid.best_estimator_

Fitting 3 folds for each of 54 candidates, totalling 162 fits
[CV] END class_weight=balanced, max_depth=6, max_features=sqrt, min_samples_split=5, n_estimators=30; total time=   0.5s
[CV] END class_weight=balanced, max_depth=6, max_features=sqrt, min_samples_split=5, n_estimators=30; total time=   0.5s
[CV] END class_weight=balanced, max_depth=6, max_features=sqrt, min_samples_split=5, n_estimators=30; total time=   0.4s
[CV] END class_weight=balanced, max_depth=6, max_features=sqrt, min_samples_split=5, n_estimators=50; total time=   0.8s
[CV] END class_weight=balanced, max_depth=6, max_features=sqrt, min_samples_split=5, n_estimators=50; total time=   0.8s
[CV] END class_weight=balanced, max_depth=6, max_features=sqrt, min_samples_split=5, n_estimators=50; total time=   0.7s
[CV] END class_weight=balanced, max_depth=6, max_features=sqrt, min_samples_split=5, n_estimators=100; total time=   1.6s
[CV] END class_weight=balanced, max_depth=6, max_features=sqrt, min_samples_split=5, n_est

In [19]:
# Entrenar modelo Random Forest 

sample_size = 5000
if len(X) > sample_size:
	X_sample = X.sample(n=sample_size, random_state=42)
	y_sample = y.loc[X_sample.index]
else:
	X_sample = X
	y_sample = y


X_sample = X_sample.astype('float32')

model = RandomForestClassifier(
	n_estimators=30,
	max_depth=8,
	max_features='sqrt',  
	min_samples_split=10, 
	random_state=42,
	n_jobs=1  
)
model.fit(X_sample, y_sample)

RandomForestClassifier(max_depth=8, min_samples_split=10, n_estimators=30,
                       n_jobs=1, random_state=42)

In [20]:
accuracy = model.score(X, y)
accuracy

0.07264880952380952

In [21]:
def generate_routine(user_profile, all_ex_df, model, encoders, seed=42):
    """
    Genera una rutina personalizada en base al perfil del usuario, tiempo disponible y variedad de grupos musculares.
    Solo utiliza ejercicios de tipo Strength.
    """
    import numpy as np

    # Validar edad
    age = user_profile['Age']
    if not 17 <= age <= 70:
        raise ValueError("La edad debe estar entre 17 y 70 años.")

    # Mapear frecuencia a días
    week_days = ['Día 1','Día 2','Día 3','Día 4','Día 5','Día 6','Día 7']
    freq = user_profile['Frequency']
    if not 1 <= freq <= 7:
        raise ValueError("Frequency debe ser un entero entre 1 y 7.")
    days = week_days[:freq]

    # Calcular ejercicios según tiempo
    total_time = user_profile.get('Workout_minutes', 60)
    warmup = 10
    rest_per_exercise = 2
    available_time = total_time - warmup
    approx_exercise_time = 5
    exercises_per_day = max(3, min(6, available_time // (approx_exercise_time + rest_per_exercise)))

    # Codificar inputs
    g = encoders['Gender'].transform([user_profile['Gender']])[0]
    l = encoders['Level'].transform([user_profile['Level']])[0]

    # Filtrar ejercicios
    df_filtered = all_ex_df[
        (all_ex_df['Gender_code'] == g) &
        (all_ex_df['Level_code'] == l) &
        (abs(all_ex_df['Age'] - age) <= 3) &
        (abs(all_ex_df['Weight_kg'] - user_profile['weight_kg']) <= 5) &
        (abs(all_ex_df['Height_m'] - user_profile['Height_m']) <= 0.05)
    ].drop_duplicates('Title').copy()

    if df_filtered.empty:
        df_filtered = all_ex_df[(all_ex_df['Level_code'] == l)].drop_duplicates('Title').copy()
    if df_filtered.empty:
        print("[⚠️ Aviso] No se encontraron ejercicios adecuados para el perfil especificado. Aplicando filtro general.")
        df_filtered = all_ex_df.drop_duplicates('Title').copy()

    # Preparar predicción
    X_pred = df_filtered.copy()
    X_pred['Gender_code'] = g
    X_pred['Level_code'] = l
    X_pred['Age'] = age
    X_pred['Weight_kg'] = user_profile['weight_kg']
    X_pred['Height_m'] = user_profile['Height_m']
    X_pred['Frequency'] = freq
    X_pred['Type_x_code'] = encoders['Type_x'].transform(['Strength'])[0]
    X_pred['BMI'] = X_pred['Weight_kg'] / (X_pred['Height_m']**2)  

    feature_cols = [
        'Age', 'Gender_code', 'Weight_kg', 'Height_m', 'Frequency', 'BMI',
        'Level_code', 'Type_x_code', 'BodyGroup_code', 'BodyPart_code', 'Equipment_code'
    ]

    if X_pred.empty or len(X_pred) < 3:
        raise ValueError("No hay suficientes ejercicios compatibles para generar una rutina.")

    # Predecir score
    proba = model.predict_proba(X_pred[feature_cols])
    title_classes = model.classes_
    scores = []
    for i, (_, row) in enumerate(X_pred.iterrows()):
        title = row['Title']
        if title in title_classes:
            class_index = list(title_classes).index(title)
            scores.append(proba[i][class_index])
        else:
            scores.append(0)
    X_pred['score'] = scores

    # Selección de ejercicios
    ranked = X_pred.sort_values('score', ascending=False).reset_index(drop=True)
    rng = np.random.RandomState(seed)
    used = set()
    schedule = {}
    prev_bodyparts = set()

    for day in days:
        chosen = []
        bodyparts_today = set()
        ptr = 0

        while len(chosen) < exercises_per_day and ptr < len(ranked):
            row = ranked.iloc[ptr]
            title = row['Title']
            bodypart = row['BodyPart']
            if title not in used and bodypart not in prev_bodyparts:
                chosen.append(f"{title} ({bodypart})")
                used.add(title)
                bodyparts_today.add(bodypart)
            ptr += 1

        # Si faltan ejercicios, permitir completar
        if len(chosen) < exercises_per_day:
            pool = ranked.head(200)
            remaining = [r for r in pool['Title'].tolist() if r not in used]
            needed = exercises_per_day - len(chosen)

            if not remaining:
                extra = rng.choice(pool['Title'].tolist(), size=needed, replace=True).tolist()
            else:
                if len(remaining) >= needed:
                    extra = rng.choice(remaining, size=needed, replace=False).tolist()
                else:
                    extra = rng.choice(remaining, size=needed, replace=True).tolist()

            for ex in extra:
                row = ranked[ranked['Title'] == ex].iloc[0]
                chosen.append(f"{row['Title']} ({row['BodyPart']})")
                used.add(ex)

        # Validar diversidad de bodyparts
        len(bodyparts_today) < 2
        #    print(f"[⚠️ Aviso] En {day}, solo se asignó 1 grupo muscular. Intenta ampliar el pool de ejercicios o ajustar filtros.")

        schedule[day] = chosen
        prev_bodyparts = bodyparts_today.copy()

    return schedule

In [22]:
if __name__ == '__main__':
    user_profile = {
        'Gender':         'Male', # Género del usuario
        'Level':          'Intermediate', # Los niveles pueden ser: Beginner, Intermediate, Advanced
        'Age':            26, # Edad del usuario (entre 17 y 70 años)
        'weight_kg':      70,
        'Height_m':       1.75,#Weight y Height para calcular el IMC y ajustar el entrenamiento a la complexión del usuario
        'Frequency':      3, # Frecuencia semanal de entrenamiento (entre 1 y 7 días)
        'Workout_minutes': 60 # tiempo total por sesión (Con tiempo de calentamiento y max 2 min de dedsanso entre ejercicios)
    }
 
    ejemplo = generate_routine(
        user_profile=user_profile,
        all_ex_df=SL,
        model=model,
        encoders=encoders,
        seed=42
    )

    print("Rutina semanal recomendada:")
    for dia, ejercicios in ejemplo.items():
        print(f"{dia}:")
        for i, ex in enumerate(ejercicios, 1):
            print(f"  {i}. {ex}")

Rutina semanal recomendada:
Día 1:
  1. FYR Banded Plank Jack (Abdominals)
  2. Band-suspended kettlebell bench press (Chest)
  3. Band-assisted chin-up (Middle Back)
  4. Decline bar press sit-up (Abdominals)
  5. Standing alternating band speed row (Forearms)
  6. UP Band Pull-Apart (Shoulders)
Día 2:
  1. Smith machine shrug (Traps)
  2. Exercise ball rear delt fly (Lower Back)
  3. Band seated row (Traps)
  4. FYR2 Standing Banded Leg Abduction (Abductors)
  5. Holman Overhead Weighted Triceps Press (Triceps)
  6. FYR2 Lateral Band Walk (Quadriceps)
Día 3:
  1. One-Arm Long Bar Row (Middle Back)
  2. Holman Plate Dynamo Push-Up (Chest)
  3. Landmine Linear Jammer (Shoulders)
  4. Weighted pull-up (Lats)
  5. 30 Barbell Roll-Out (Abdominals)
  6. Band standing concentration curl (Biceps)


El accuracy bajo refleja la dificultad del problema, no necesariamente un mal modelo.
Lo importante es que el modelo ayude a recomendar ejercicios relevantes y variados, no solo acertar el único correcto. es fundamental recalcar que en sistemas de recomendación el objetivo principal no es necesariamente acertar el ejercicio exacto, sino proporcionar un conjunto de sugerencias relevantes, variadas y adaptadas al usuario.

In [ ]:
joblib.dump({
    'model': model,
    'encoders': encoders,
    'all_ex_df': SL
}, "SmartLifter.pkl")
print("SmartLifter.pkl guardado correctamente.")

SmartLifter.pkl guardado correctamente.


In [24]:
SL['BodyPart'].unique()

array(['Abdominals', 'Abductors', 'Biceps', 'Calves', 'Chest', 'Forearms',
       'Glutes', 'Hamstrings', 'Lats', 'Lower Back', 'Middle Back',
       'Neck', 'Traps', 'Quadriceps', 'Shoulders', 'Triceps', 'Adductors'],
      dtype=object)